In [11]:
import pandas as pd
import numpy as np
from bs4 import BeautifulSoup
from nltk import sent_tokenize
from nltk import word_tokenize
import re
import requests
from sentence_transformers import SentenceTransformer, util
import nltk
import string
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')
import torch
import yake

In [394]:
planes_vlc = pd.read_csv("planes_vlc.csv")
plans_chg = pd.read_csv("plans_chg.csv")

In [396]:
plans = plans_chg['DS_PLAN'].tolist()

In [397]:
# Convierte todos los elementos a minúsculas
plans_l = [text.lower() for text in plans]

In [398]:
# Crea una máscara de traducción para eliminar los signos de puntuación
translator = str.maketrans('', '', string.punctuation)

# Aplica la máscara a cada elemento de la lista
plans_p = [elemento.translate(translator) for elemento in plans_l]

# Ahora, lista_sin_puntuacion contiene los elementos sin signos de puntuación
print(plans_p)

['fever gift card  chicago', 'drunk shakespeare chicago', 'candlelight gift card  chicago', 'mystery picnic date selfguided foodie adventure  chicago', 'mystery picnic with friends self guided foodie adventure  chicago', 'spray paint n sip urban art workshop', 'deepdish pizza tour in chicago with local expert', 'the escape game chicago epic 60minute adventures', 'underground donut tour  chicagos first donut tour', 'private sunset sail on lake michigan with breathtaking views of chicago', 'rosemont indoor skydiving 2 flights  certificate', 'bikes bites and brews chicagos signature dishes bike tour', 'chicago architecture center exhibits admission', 'offbeat street art tour of chicago urban graffiti and murals', 'pizza city usa west loop pizza crawl', 'chicago bike rental', 'field museum of natural history allaccess pass', 'chicago loop scavenger hunt', 'chicago architecture center river cruise', 'chicago crime and mob tour', 'lincoln park indoor skydiving 2 flights  certificate', 'chica

In [399]:
# Lista para almacenar los tokens de cada texto
plans_tkn = []

# Tokeniza cada texto y agrega la lista de tokens a lista_de_listas_de_tokens
for text in plans_p:
    tokens = word_tokenize(text)
    plans_tkn.append(tokens)

# Ahora, lista_de_listas_de_tokens contiene listas de tokens para cada texto
for tokens in plans_tkn:
    print(tokens)

['fever', 'gift', 'card', 'chicago']
['drunk', 'shakespeare', 'chicago']
['candlelight', 'gift', 'card', 'chicago']
['mystery', 'picnic', 'date', 'selfguided', 'foodie', 'adventure', 'chicago']
['mystery', 'picnic', 'with', 'friends', 'self', 'guided', 'foodie', 'adventure', 'chicago']
['spray', 'paint', 'n', 'sip', 'urban', 'art', 'workshop']
['deepdish', 'pizza', 'tour', 'in', 'chicago', 'with', 'local', 'expert']
['the', 'escape', 'game', 'chicago', 'epic', '60minute', 'adventures']
['underground', 'donut', 'tour', 'chicagos', 'first', 'donut', 'tour']
['private', 'sunset', 'sail', 'on', 'lake', 'michigan', 'with', 'breathtaking', 'views', 'of', 'chicago']
['rosemont', 'indoor', 'skydiving', '2', 'flights', 'certificate']
['bikes', 'bites', 'and', 'brews', 'chicagos', 'signature', 'dishes', 'bike', 'tour']
['chicago', 'architecture', 'center', 'exhibits', 'admission']
['offbeat', 'street', 'art', 'tour', 'of', 'chicago', 'urban', 'graffiti', 'and', 'murals']
['pizza', 'city', 'usa',

In [400]:
stop_words = set(stopwords.words('english')) # Set of stopwords
# stop_words = set(stopwords.words('spanish')) # Set of stopwords

In [401]:
plans_sw = []

# Iterar a través de las listas de tokens y aplicar la eliminación de stopwords
for words in plans_tkn:
    tkn_sw = [word for word in words if word not in stop_words]
    plans_sw.append(tkn_sw)

# Ahora, lista_de_listas_de_tokens_sin_stopwords contiene listas de tokens sin stopwords
for text_sw in plans_sw:
    print(text_sw)

['fever', 'gift', 'card', 'chicago']
['drunk', 'shakespeare', 'chicago']
['candlelight', 'gift', 'card', 'chicago']
['mystery', 'picnic', 'date', 'selfguided', 'foodie', 'adventure', 'chicago']
['mystery', 'picnic', 'friends', 'self', 'guided', 'foodie', 'adventure', 'chicago']
['spray', 'paint', 'n', 'sip', 'urban', 'art', 'workshop']
['deepdish', 'pizza', 'tour', 'chicago', 'local', 'expert']
['escape', 'game', 'chicago', 'epic', '60minute', 'adventures']
['underground', 'donut', 'tour', 'chicagos', 'first', 'donut', 'tour']
['private', 'sunset', 'sail', 'lake', 'michigan', 'breathtaking', 'views', 'chicago']
['rosemont', 'indoor', 'skydiving', '2', 'flights', 'certificate']
['bikes', 'bites', 'brews', 'chicagos', 'signature', 'dishes', 'bike', 'tour']
['chicago', 'architecture', 'center', 'exhibits', 'admission']
['offbeat', 'street', 'art', 'tour', 'chicago', 'urban', 'graffiti', 'murals']
['pizza', 'city', 'usa', 'west', 'loop', 'pizza', 'crawl']
['chicago', 'bike', 'rental']
['fi

In [404]:
# Convierte la lista de listas en una serie de pandas
plans_sw_serie = pd.Series(plans_sw)

# Agrega la nueva columna al DataFrame
plans_chg['tokens'] = plans_sw_serie

# Imprime el DataFrame resultante
print(plans_chg)

     ID_PLAN                                            DS_PLAN  DS_CITY  \
0      79644                          Fever Gift Card - Chicago  Chicago   
1      79866                         Drunk Shakespeare Chicago!  Chicago   
2      84889                    Candlelight Gift Card - Chicago  Chicago   
3      89086  Mystery Picnic Date: Self-Guided Foodie Advent...  Chicago   
4      89087  Mystery Picnic with Friends: Self Guided Foodi...  Chicago   
..       ...                                                ...      ...   
143   139226                          Chicago Vampire Ball 2023  Chicago   
144   139474                 The Nun II - AMC Tickets - Chicago  Chicago   
145   139475   My Big Fat Greek Wedding 3 AMC Tickets - Chicago  Chicago   
146   139926         A Haunting in Venice AMC Tickets - Chicago  Chicago   
147   139942   Perceptual Experience Interactive Art Exhibition  Chicago   

                                            TAXONOMIES  \
0    Other Mixed, Low Intensi

In [406]:
# Define las configuraciones del extractor de palabras clave YAKE
language = "en"
max_ngram_size = 5
deduplication_threshold = 0.9
numOfKeywords = 20
custom_kw_extractor = yake.KeywordExtractor(lan=language, n=max_ngram_size, dedupLim=deduplication_threshold, top=numOfKeywords, features=None)

# Lista para almacenar todas las palabras clave de todas las listas
todas_las_palabras_clave = []

# Itera a través de las listas de tokens sin stopwords y aplica YAKE
for index, row in plans_chg.iterrows():
    lista_tokens = row['tokens']
    texto = " ".join(lista_tokens)
    keywords = custom_kw_extractor.extract_keywords(texto)
    
    # Filtra las palabras clave que tienen dos o más palabras (no son unigramas)
    # keywords_sin_unigramas = [kw for kw in keywords if ' ' in kw[0]]

    # Agrega el código ID_PLAN a cada palabra clave generada
    keywords_con_id = [(row['ID_PLAN'], kw[0], kw[1]) for kw in keywords]
    
    # Extiende la lista principal con las palabras clave de esta lista
    todas_las_palabras_clave.extend(keywords_con_id)

# Imprime todas las palabras clave en una sola lista
for kw in todas_las_palabras_clave:
    print(f"ID_PLAN: {kw[0]}, Palabra Clave: {kw[1]}, Puntuación: {kw[2]}")


ID_PLAN: 79644, Palabra Clave: fever gift card chicago, Puntuación: 0.0028511136585327272
ID_PLAN: 79644, Palabra Clave: fever gift card, Puntuación: 0.01655915082773619
ID_PLAN: 79644, Palabra Clave: gift card chicago, Puntuación: 0.016559150827736194
ID_PLAN: 79644, Palabra Clave: fever gift, Puntuación: 0.04940384002065631
ID_PLAN: 79644, Palabra Clave: card chicago, Puntuación: 0.04940384002065631
ID_PLAN: 79644, Palabra Clave: gift card, Puntuación: 0.09700399286574239
ID_PLAN: 79644, Palabra Clave: fever, Puntuación: 0.15831692877998726
ID_PLAN: 79644, Palabra Clave: chicago, Puntuación: 0.15831692877998726
ID_PLAN: 79644, Palabra Clave: gift, Puntuación: 0.29736558256021506
ID_PLAN: 79644, Palabra Clave: card, Puntuación: 0.29736558256021506
ID_PLAN: 79866, Palabra Clave: drunk shakespeare chicago, Puntuación: 0.008321268142839145
ID_PLAN: 79866, Palabra Clave: drunk shakespeare, Puntuación: 0.04940384002065631
ID_PLAN: 79866, Palabra Clave: shakespeare chicago, Puntuación: 0.04

In [407]:
url = input("Insert the URL to search for Fever plans.")

# Realizar la solicitud HTTP
get_url = requests.get(url)
get_text = get_url.text
soup = BeautifulSoup(get_text, "html.parser")

# Buscar la sección 'article__body col-md-8'
all_content = soup.find("section", class_="article__body col-md-8")

# Buscar todos los elementos <p> y <h2>
text_elements = all_content.find_all(['p', 'h2'])

paragraphs = []
# Expresión regular para detectar emoticonos
emoji_pattern = re.compile(r'[\U0001F600-\U0001F64F\U0001F300-\U0001F5FF\U0001F680-\U0001F6FF\U0001F700-\U0001F77F\U0001F1E0-\U0001F1FF\U00002702-\U000027B0\U000024C2-\U0001F251]+')

for element in text_elements:
    if element.name == 'p':
        if element.get_text(strip=True) == '':
            continue
        # Filtrar los párrafos que no contienen imágenes ni emoticonos
        if not element.find('img') and not emoji_pattern.search(element.get_text()):
            if not element.find_parent('blockquote') and not element.find_parent('iframe', class_='instagram-media instagram-media-rendered'):
                paragraphs.append(element.get_text())
    elif element.name == 'h2':
        paragraphs.append(element.get_text())

# Imprimir los párrafos y encabezados <h2>
for paragraph in paragraphs:
    print(paragraph)

September is here and the summer weather is about to transition into autumn cheer. For now, though, there are still plenty more days of summer, and on the back of the recent record-breaking highs the weather is certainly still allowing us to frolic in September sunshine.
Patios are alive and kicking, museums are announcing free days and all that fall fun is beginning to announce itself. On top of that, there are unmissable one-off events like Labor Day celebrations and the Autumn Equinox.
Here are the best things to do in Chicago this September!
1. Embrace the peak of patio season at Chicago’s largest patio
Despite the end of summer on the horizon, it’s still very much the perfect weather to kick back on a patio. Chicago doesn’t play around when it comes to patio season. Come rain or shine, if a patio is opened somewhere in the Windy City, guaranteed Chicagoans are out there clinking drinks.
We’ve rounded up the very best patios and beer gardens in and around Chicago to give you an ess

In [408]:
# Lista para almacenar los resultados
arts = []

# Iterar sobre cada texto y aplicar el proceso de preprocesamiento
for text in paragraphs:
   
    # Tokenización
    tokens = sent_tokenize(text)

    def remove_punctuation(sentence):
        return re.sub(r'[^\w\s]', '', sentence)

    # Aplicar la función a todas las frases
    sents = [remove_punctuation(sentence) for sentence in tokens]

    arts.append(sents) 
    

# Imprimir los resultados procesados
for idx, processed_text in enumerate(arts):
    print(f"Processed Text {idx+1}: {processed_text}")

Processed Text 1: ['September is here and the summer weather is about to transition into autumn cheer', 'For now though there are still plenty more days of summer and on the back of the recent recordbreaking highs the weather is certainly still allowing us to frolic in September sunshine']
Processed Text 2: ['Patios are alive and kicking museums are announcing free days and all that fall fun is beginning to announce itself', 'On top of that there are unmissable oneoff events like Labor Day celebrations and the Autumn Equinox']
Processed Text 3: ['Here are the best things to do in Chicago this September']
Processed Text 4: ['1', 'Embrace the peak of patio season at Chicagos largest patio']
Processed Text 5: ['Despite the end of summer on the horizon its still very much the perfect weather to kick back on a patio', 'Chicago doesnt play around when it comes to patio season', 'Come rain or shine if a patio is opened somewhere in the Windy City guaranteed Chicagoans are out there clinking d

In [409]:
def convertir_listas_a_minusculas(listas):
    for lista in listas:
        for i in range(len(lista)):
            lista[i] = lista[i].lower()

# Convertir las listas a minúsculas
if arts:
    convertir_listas_a_minusculas(arts)

    # Imprimir las listas modificadas
    for lista in arts:
        print(lista)

['september is here and the summer weather is about to transition into autumn cheer', 'for now though there are still plenty more days of summer and on the back of the recent recordbreaking highs the weather is certainly still allowing us to frolic in september sunshine']
['patios are alive and kicking museums are announcing free days and all that fall fun is beginning to announce itself', 'on top of that there are unmissable oneoff events like labor day celebrations and the autumn equinox']
['here are the best things to do in chicago this september']
['1', 'embrace the peak of patio season at chicagos largest patio']
['despite the end of summer on the horizon its still very much the perfect weather to kick back on a patio', 'chicago doesnt play around when it comes to patio season', 'come rain or shine if a patio is opened somewhere in the windy city guaranteed chicagoans are out there clinking drinks']
['weve rounded up the very best patios and beer gardens in and around chicago to g

In [410]:
# Función para tokenizar las palabras en todas las listas
def tokenizar_listas(listas):
    arts_tkn = []
    for lista in arts:
        tokens = [word_tokenize(word) for word in lista]
        arts_tkn.append(tokens)
    return arts_tkn

# Tokenizar las listas
if arts:
    arts_tkn = tokenizar_listas(arts)

    # Imprimir las listas tokenizadas
    for lista in arts_tkn:
        print(lista)

[['september', 'is', 'here', 'and', 'the', 'summer', 'weather', 'is', 'about', 'to', 'transition', 'into', 'autumn', 'cheer'], ['for', 'now', 'though', 'there', 'are', 'still', 'plenty', 'more', 'days', 'of', 'summer', 'and', 'on', 'the', 'back', 'of', 'the', 'recent', 'recordbreaking', 'highs', 'the', 'weather', 'is', 'certainly', 'still', 'allowing', 'us', 'to', 'frolic', 'in', 'september', 'sunshine']]
[['patios', 'are', 'alive', 'and', 'kicking', 'museums', 'are', 'announcing', 'free', 'days', 'and', 'all', 'that', 'fall', 'fun', 'is', 'beginning', 'to', 'announce', 'itself'], ['on', 'top', 'of', 'that', 'there', 'are', 'unmissable', 'oneoff', 'events', 'like', 'labor', 'day', 'celebrations', 'and', 'the', 'autumn', 'equinox']]
[['here', 'are', 'the', 'best', 'things', 'to', 'do', 'in', 'chicago', 'this', 'september']]
[['1'], ['embrace', 'the', 'peak', 'of', 'patio', 'season', 'at', 'chicagos', 'largest', 'patio']]
[['despite', 'the', 'end', 'of', 'summer', 'on', 'the', 'horizon',

In [411]:
# Función para eliminar stopwords de una lista de palabras tokenizadas
def eliminar_stopwords_de_lista(lista_tokenizada):
    # stop_words = set(stopwords.words("english"))  # Puedes cambiar "english" por otro idioma si es necesario
    lista_sin_stopwords = [palabra for palabra in lista_tokenizada if palabra.lower() not in stop_words]
    return lista_sin_stopwords

# Función para combinar palabras en una lista en una sola frase
def combinar_palabras_en_frase(lista_palabras):
    frase = " ".join(lista_palabras)
    return [frase]

# Procesar la estructura de tres niveles y almacenar los resultados en una nueva lista
resultado_final = []
for lista_de_listas in arts_tkn:
    lista_resultado_nivel_1 = []
    for lista in lista_de_listas:
        lista_sin_stopwords = eliminar_stopwords_de_lista(lista)
        frase = combinar_palabras_en_frase(lista_sin_stopwords)
        lista_resultado_nivel_1.extend(frase)
    resultado_final.extend(lista_resultado_nivel_1)

# Imprimir el resultado final
for frase in resultado_final:
    print(frase)

september summer weather transition autumn cheer
though still plenty days summer back recent recordbreaking highs weather certainly still allowing us frolic september sunshine
patios alive kicking museums announcing free days fall fun beginning announce
top unmissable oneoff events like labor day celebrations autumn equinox
best things chicago september
1
embrace peak patio season chicagos largest patio
despite end summer horizon still much perfect weather kick back patio
chicago doesnt play around comes patio season
come rain shine patio opened somewhere windy city guaranteed chicagoans clinking drinks
weve rounded best patios beer gardens around chicago give essential range options one thats ideal soaking last summer sun recesss gigantic patio bar
nestled within 30 shipping containers west loop corner recess home cozy amalgamation bars food stands cabana houses within 14500squarefoot space holds title largest patio chicago
stacked shipping containers give awesome reclaimed industrial

In [412]:
# Lista para almacenar resultados
resu_all = []

# Recorrer cada keyword de todas_las_palabras_clave
for id, keyword, puntuacion in todas_las_palabras_clave:
    for frase in resultado_final:
        # Verificar si la keyword está presente en la frase (ignorar mayúsculas y minúsculas)
        if keyword in frase:
            resu_all.append((id, keyword, puntuacion, frase))

# Imprimir los resultados
for resultado in resu_all:
    id, keyword, puntuacion, frase = resultado
    print(f"PLAN_ID: {id}, Keyword: {keyword}, Puntuación: {puntuacion}, Frase: {frase}")

PLAN_ID: 79644, Keyword: gift card, Puntuación: 0.09700399286574239, Frase: candlelight gift cards easy use valid candlelight event us making unique gift friends family
PLAN_ID: 79644, Keyword: chicago, Puntuación: 0.15831692877998726, Frase: best things chicago september
PLAN_ID: 79644, Keyword: chicago, Puntuación: 0.15831692877998726, Frase: embrace peak patio season chicagos largest patio
PLAN_ID: 79644, Keyword: chicago, Puntuación: 0.15831692877998726, Frase: chicago doesnt play around comes patio season
PLAN_ID: 79644, Keyword: chicago, Puntuación: 0.15831692877998726, Frase: come rain shine patio opened somewhere windy city guaranteed chicagoans clinking drinks
PLAN_ID: 79644, Keyword: chicago, Puntuación: 0.15831692877998726, Frase: weve rounded best patios beer gardens around chicago give essential range options one thats ideal soaking last summer sun recesss gigantic patio bar
PLAN_ID: 79644, Keyword: chicago, Puntuación: 0.15831692877998726, Frase: nestled within 30 shippin

In [ ]:
# Lista para almacenar resultados
resultados = []

# Recorrer cada keyword de todas_las_palabras_clave
for keyword, puntuacion in todas_las_palabras_clave:
    for frase in resultado_final:
        # Dividir la frase en palabras
        palabras = frase.split()
        
        # Verificar si la keyword está presente en la lista de palabras (ignorar mayúsculas y minúsculas)
        if keyword in [palabra for palabra in palabras]:
            resultados.append((keyword, puntuacion, frase))

# Imprimir los resultados
for resultado in resultados:
    keyword, puntuacion, frase = resultado
    print(f"Keyword: {keyword}, Puntuación: {puntuacion}, Frase: {frase}")

In [413]:
# Extraer los primeros elementos de cada tupla
kws = [tupla[1] for tupla in todas_las_palabras_clave]

# Imprimir la lista resultante
print(kws)

['fever gift card chicago', 'fever gift card', 'gift card chicago', 'fever gift', 'card chicago', 'gift card', 'fever', 'chicago', 'gift', 'card', 'drunk shakespeare chicago', 'drunk shakespeare', 'shakespeare chicago', 'drunk', 'chicago', 'shakespeare', 'candlelight gift card chicago', 'candlelight gift card', 'gift card chicago', 'candlelight gift', 'card chicago', 'gift card', 'candlelight', 'chicago', 'gift', 'card', 'mystery picnic date selfguided foodie', 'date selfguided foodie adventure chicago', 'picnic date selfguided foodie adventure', 'mystery picnic date selfguided', 'selfguided foodie adventure chicago', 'picnic date selfguided foodie', 'date selfguided foodie adventure', 'mystery picnic date', 'foodie adventure chicago', 'picnic date selfguided', 'date selfguided foodie', 'selfguided foodie adventure', 'mystery picnic', 'adventure chicago', 'picnic date', 'date selfguided', 'selfguided foodie', 'foodie adventure', 'mystery', 'chicago', 'mystery picnic friends self guided

In [414]:
# Lista de cadenas originales
cadena_original = kws

# Lista de cadenas contenedoras
cadena_contenedora = resultado_final

# Usar expresión regular para encontrar la palabra completa en cada elemento de la lista
resu_word = []

for original in cadena_original:
    patron = r'\b\w*' + re.escape(original) + r'\w*\b'
    for contenedora in cadena_contenedora:
        resultado = re.search(patron, contenedora, re.IGNORECASE)
        if resultado:
            palabra_completa = resultado.group()
            resu_word.append((original, palabra_completa, contenedora))

# Imprimir los resultados
for original, palabra_completa, contenedora in resu_word:
    print(f"Cadena original: {original}, Palabra completa: {palabra_completa}, Frase completa: {contenedora}")


Cadena original: gift card, Palabra completa: gift cards, Frase completa: candlelight gift cards easy use valid candlelight event us making unique gift friends family
Cadena original: chicago, Palabra completa: chicago, Frase completa: best things chicago september
Cadena original: chicago, Palabra completa: chicagos, Frase completa: embrace peak patio season chicagos largest patio
Cadena original: chicago, Palabra completa: chicago, Frase completa: chicago doesnt play around comes patio season
Cadena original: chicago, Palabra completa: chicagoans, Frase completa: come rain shine patio opened somewhere windy city guaranteed chicagoans clinking drinks
Cadena original: chicago, Palabra completa: chicago, Frase completa: weve rounded best patios beer gardens around chicago give essential range options one thats ideal soaking last summer sun recesss gigantic patio bar
Cadena original: chicago, Palabra completa: chicago, Frase completa: nestled within 30 shipping containers west loop corne

In [415]:
# Lista para almacenar resultados
active_plans = []

# Comparar y agregar elementos a la lista active_plans
for tupla_all, tupla_word in zip(resu_all, resu_word):
    if tupla_all[1] == tupla_word[1]:
        active_plans.append((tupla_all[0], tupla_all[1], tupla_word[2]))

# Imprimir la lista active_plans
for item in active_plans:
    print(item)

(79644, 'chicago', 'best things chicago september')
(79644, 'chicago', 'chicago doesnt play around comes patio season')
(79644, 'chicago', 'weve rounded best patios beer gardens around chicago give essential range options one thats ideal soaking last summer sun recesss gigantic patio bar')
(79644, 'chicago', 'nestled within 30 shipping containers west loop corner recess home cozy amalgamation bars food stands cabana houses within 14500squarefoot space holds title largest patio chicago')
(79644, 'chicago', 'read recess chicago')
(79644, 'chicago', 'youre serious corn maze exploration largest corn maze world opens far chicago saturday september 9')
(79644, 'chicago', 'chicago built grid system streets lining near perfectly compass north south east west sun lines directly chicagos eastwest facing streets beams heart city splashing chicagos artificial valleys')
(79644, 'chicago', 'loads going labor day year find plenty options roundup amazing things labor day weekend chicago')
(79644, 'chi

In [416]:
active_plans = pd.DataFrame(active_plans, columns=["ID_PLAN", "KW", "TEXT"])

In [419]:
# Combinar DataFrames en función de la columna 'ID_PLAN'
active_plans = active_plans.merge(plans_chg[['ID_PLAN', 'DS_PLAN']], on='ID_PLAN', how='left')

# Imprimir el DataFrame resultante
# active_plans

ID_PLAN       KW                                               TEXT  \
0       79644  chicago                      best things chicago september   
1       79644  chicago      chicago doesnt play around comes patio season   
2       79644  chicago  weve rounded best patios beer gardens around c...   
3       79644  chicago  nestled within 30 shipping containers west loo...   
4       79644  chicago                                read recess chicago   
...       ...      ...                                                ...   
5579   139942      art  hunting mustsee street art murals chicago rewa...   
5580   139942      art  alternatively also jump offbeat street art tou...   
5581   139942      art  perusing chicagos incredible street art creati...   
5582   139942      art  grab tickets spray paint n sip urban art workshop   
5583   139942      art  foodies prefer sample tasty delicacies perusin...   

                                               DS_PLAN  
0                            Fever Gift Card - Chicago  
1                            Fever Gift Card - Chicago  
2                            Fever Gift Card - Chicago  
3                            Fever Gift Card - Chicago  
4                            Fever Gift Card - Chicago  
...                                                ...  
5579  Perceptual Experience Interactive Art Exhibition  
5580  Perceptual Experience Interactive Art Exhibition  
5581  Perceptual Experience Interactive Art Exhibition  
5582  Perceptual Experience Interactive Art Exhibition  
5583  Perceptual Experience Interactive Art Exhibition  

[5584 rows x 4 columns]

In [421]:
# Función para realizar la limpieza de texto
def clean_text(text):
    # Eliminar signos de puntuación
    text = text.translate(str.maketrans('', '', string.punctuation))
    
    # Convertir a minúsculas
    text = text.lower()
    
    # Tokenizar el texto en palabras
    words = text.split()
    
    # Eliminar stopwords en español
    # stop_words = set(stopwords.words('spanish'))
    words = [word for word in words if word not in stop_words]
    
    # Unir las palabras nuevamente en un solo texto
    cleaned_text = ' '.join(words)
    
    return cleaned_text

# Aplicar la función de limpieza a la columna 'DS_PLAN'
active_plans['DS_PLAN'] = active_plans['DS_PLAN'].apply(clean_text)

# Imprimir el DataFrame resultante
active_plans

ID_PLAN       KW                                               TEXT  \
0       79644  chicago                      best things chicago september   
1       79644  chicago      chicago doesnt play around comes patio season   
2       79644  chicago  weve rounded best patios beer gardens around c...   
3       79644  chicago  nestled within 30 shipping containers west loo...   
4       79644  chicago                                read recess chicago   
...       ...      ...                                                ...   
5579   139942      art  hunting mustsee street art murals chicago rewa...   
5580   139942      art  alternatively also jump offbeat street art tou...   
5581   139942      art  perusing chicagos incredible street art creati...   
5582   139942      art  grab tickets spray paint n sip urban art workshop   
5583   139942      art  foodies prefer sample tasty delicacies perusin...   

                                               DS_PLAN  
0                              fever gift card chicago  
1                              fever gift card chicago  
2                              fever gift card chicago  
3                              fever gift card chicago  
4                              fever gift card chicago  
...                                                ...  
5579  perceptual experience interactive art exhibition  
5580  perceptual experience interactive art exhibition  
5581  perceptual experience interactive art exhibition  
5582  perceptual experience interactive art exhibition  
5583  perceptual experience interactive art exhibition  

[5584 rows x 4 columns]

In [422]:
# Filtrar las filas que no contienen "Valencia" en la columna KW
active_plans_filtrado = active_plans.loc[~active_plans['KW'].str.contains('chicago')]

# Imprimir el DataFrame resultante
# active_plans_filtrado

ID_PLAN                 KW  \
62      79644               gift   
63      79644               gift   
64      79866  drunk shakespeare   
65      79866  drunk shakespeare   
66      79866  drunk shakespeare   
...       ...                ...   
5579   139942                art   
5580   139942                art   
5581   139942                art   
5582   139942                art   
5583   139942                art   

                                                   TEXT  \
62    cant decide concert want ensure attend one nee...   
63    candlelight gift cards easy use valid candleli...   
64                        buckel drunk shakespeare show   
65    topic booze another brilliant chicago experien...   
66    five classicallytrained actors meet members dr...   
...                                                 ...   
5579  hunting mustsee street art murals chicago rewa...   
5580  alternatively also jump offbeat street art tou...   
5581  perusing chicagos incredible street art creati...   
5582  grab tickets spray paint n sip urban art workshop   
5583  foodies prefer sample tasty delicacies perusin...   

                                               DS_PLAN  
62                             fever gift card chicago  
63                             fever gift card chicago  
64                           drunk shakespeare chicago  
65                           drunk shakespeare chicago  
66                           drunk shakespeare chicago  
...                                                ...  
5579  perceptual experience interactive art exhibition  
5580  perceptual experience interactive art exhibition  
5581  perceptual experience interactive art exhibition  
5582  perceptual experience interactive art exhibition  
5583  perceptual experience interactive art exhibition  

[1648 rows x 4 columns]

In [423]:
# Model Selection and Initialization
# model = SentenceTransformer('distiluse-base-multilingual-cased-v1')
model = SentenceTransformer('paraphrase-multilingual-mpnet-base-v2') 
# model = SentenceTransformer('paraphrase-xlm-r-multilingual-v1')
# Crear una lista de diccionarios para almacenar los resultados
fever_plans = []

# Iterar a través de las filas del DataFrame df_sin_duplicados
for index, row in active_plans_filtrado.iterrows():
    sentence1 = row['TEXT']
    sentence2 = row['DS_PLAN']
    
    # Encode sentences to get their embeddings
    embedding1 = model.encode(sentence1, convert_to_tensor=True)
    embedding2 = model.encode(sentence2, convert_to_tensor=True)

    # Compute similarity score of two embeddings
    cosine_scores = util.pytorch_cos_sim(embedding1, embedding2)
    similarity_score = cosine_scores.item()
    
    # Crear un diccionario con los resultados y agregarlo a la lista
    result_dict = {
        'ID_PLAN': row['ID_PLAN'],
        'KW': row['KW'],
        'TEXT': sentence1,
        'DS_PLAN': sentence2,
        'SCORE': similarity_score
    }
    fever_plans.append(result_dict)

# Convertir la lista de diccionarios en un DataFrame
fever_plans_df = pd.DataFrame(fever_plans)

# Imprimir el DataFrame resultante
# fever_plans_df

ID_PLAN                 KW  \
0       79644               gift   
1       79644               gift   
2       79866  drunk shakespeare   
3       79866  drunk shakespeare   
4       79866  drunk shakespeare   
...       ...                ...   
1643   139942                art   
1644   139942                art   
1645   139942                art   
1646   139942                art   
1647   139942                art   

                                                   TEXT  \
0     cant decide concert want ensure attend one nee...   
1     candlelight gift cards easy use valid candleli...   
2                         buckel drunk shakespeare show   
3     topic booze another brilliant chicago experien...   
4     five classicallytrained actors meet members dr...   
...                                                 ...   
1643  hunting mustsee street art murals chicago rewa...   
1644  alternatively also jump offbeat street art tou...   
1645  perusing chicagos incredible street art creati...   
1646  grab tickets spray paint n sip urban art workshop   
1647  foodies prefer sample tasty delicacies perusin...   

                                               DS_PLAN     SCORE  
0                              fever gift card chicago  0.309624  
1                              fever gift card chicago  0.379252  
2                            drunk shakespeare chicago  0.851326  
3                            drunk shakespeare chicago  0.800309  
4                            drunk shakespeare chicago  0.677472  
...                                                ...       ...  
1643  perceptual experience interactive art exhibition  0.447840  
1644  perceptual experience interactive art exhibition  0.506009  
1645  perceptual experience interactive art exhibition  0.520361  
1646  perceptual experience interactive art exhibition  0.468288  
1647  perceptual experience interactive art exhibition  0.340132  

[1648 rows x 5 columns]

In [426]:
# Filtrar el DataFrame usando la función query
filtered_df = fever_plans_df.query('SCORE > 0.61')

# Imprimir el DataFrame resultante
# filtered_df

ID_PLAN                 KW  \
2       79866  drunk shakespeare   
3       79866  drunk shakespeare   
4       79866  drunk shakespeare   
5       79866  drunk shakespeare   
6       79866              drunk   
...       ...                ...   
1487   137779               tour   
1506   138026              stars   
1508   138026               gift   
1580   139474            tickets   
1583   139474            tickets   

                                                   TEXT  \
2                         buckel drunk shakespeare show   
3     topic booze another brilliant chicago experien...   
4     five classicallytrained actors meet members dr...   
5                   grab tickets drunk shakespeare show   
6                         buckel drunk shakespeare show   
...                                                 ...   
1487  local host take along scenic tour chicagos fam...   
1506                               attend concert stars   
1508  cant decide concert want ensure attend one nee...   
1580                                       grab tickets   
1583            grab tickets show laugh factory chicago   

                            DS_PLAN     SCORE  
2         drunk shakespeare chicago  0.851326  
3         drunk shakespeare chicago  0.800309  
4         drunk shakespeare chicago  0.677472  
5         drunk shakespeare chicago  0.679186  
6         drunk shakespeare chicago  0.851326  
...                             ...       ...  
1487  best chicago small group tour  0.630609  
1506       concerts stars gift card  0.721946  
1508       concerts stars gift card  0.723162  
1580     nun ii amc tickets chicago  0.666494  
1583     nun ii amc tickets chicago  0.682318  

[345 rows x 5 columns]

In [427]:
# Agrupar por 'ID_PLAN' y calcular la media de los 'SCORE' en cada grupo
mean_scores_df = filtered_df.groupby('ID_PLAN').agg({'SCORE': 'mean', 'DS_PLAN': 'first'}).reset_index()

# Renombrar la columna 'SCORE' como 'MEAN_SCORE'
mean_scores_df = mean_scores_df.rename(columns={'SCORE': 'MEAN_SCORE'})

# Ordenar el DataFrame por la columna 'MEAN_SCORE' en orden descendente
mean_scores_df = mean_scores_df.sort_values(by='MEAN_SCORE', ascending=False)

# Reiniciar el índice del DataFrame resultante
mean_scores_df = mean_scores_df.reset_index(drop=True)

# Imprimir el DataFrame resultante
mean_scores_df



ID_PLAN  MEAN_SCORE                                            DS_PLAN
0     92280    0.884650        chicago instagram walking tour famous spots
1     91530    0.862871               spray paint n sip urban art workshop
2    111781    0.843858                museum contemporary art chicago mca
3     91888    0.797846  bikes bites brews chicagos signature dishes bi...
4     91882    0.776382   underground donut tour chicagos first donut tour
5     92163    0.776222  offbeat street art tour chicago urban graffiti...
6     92278    0.768033                  chicago architecture walking tour
7    131534    0.767872                   chicago history museum admission
8     79866    0.752073                          drunk shakespeare chicago
9    133980    0.743690                     chicago architecture walk time
10   124312    0.734435                                 grand cabaret dark
11    92173    0.723663  lincoln park indoor skydiving 2 flights certif...
12   138026    0.722554                           concerts stars gift card
13    84889    0.718216                      candlelight gift card chicago
14   134007    0.701154                santas village amusement water park
15    92253    0.696593          museum contemporary art general admission
16    92249    0.695071               chicago lake river architecture tour
17   133064    0.694238                               clue walking mystery
18    92284    0.690682               chicago river boat architecture tour
19    91884    0.688994  private sunset sail lake michigan breathtaking...
20   133779    0.685027  chicago 45 minute river architectural cruise tour
21   133786    0.678614                        tiffany chicago guided tour
22   139474    0.674406                         nun ii amc tickets chicago
23   133768    0.673247  chicago architecture river cruise michigan avenue
24   133784    0.672925        chicago premier dinner cruise chicago river
25    91880    0.669250           deepdish pizza tour chicago local expert
26   135517    0.668060  chicago 90minute urban adventure river lake cr...
27   133778    0.666000            chicago seadog lakefront speedboat tour
28   134741    0.665261                         barbie amc tickets chicago
29    92171    0.664419           chicago architecture center river cruise
30   127721    0.661143                       candlelight tribute coldplay
31   103434    0.660723             chicago river floating tiki bar cruise
32    91886    0.655201    rosemont indoor skydiving 2 flights certificate
33   110872    0.654242                    art institute chicago fast pass
34   118750    0.653151                                 chicago pizza tour
35   134757    0.652976       marvels advance amc tickets waitlist chicago
36   118754    0.651051               chicagos chinatown food walking tour
37   121136    0.646263                            stand stand comedy show
38   123502    0.644010                premier dinner cruise lake michigan
39   131979    0.641834                                peep show burlesque
40   106207    0.641339                      bbq drag brunch grand cabaret
41   101404    0.641095                    newport peekeasy burlesque show
42   134003    0.640369        chicago architecture river cruise navy pier
43   133757    0.639310                    medieval torture museum chicago
44   119350    0.638329                 art future holographic art gallery
45   135553    0.634639        hidden plain sight chicago prohibition tour
46   133975    0.634427                      go city chicago explorer pass
47   105164    0.633988               ghosts chicago city exploration game
48    92159    0.632830     chicago architecture center exhibits admission
49   134740    0.627088                     amc food drink tickets chicago
50   137779    0.626231                      best chicago small group tour
51    92283    0.624999                      chicago loop secret food tour
52   135611    0.624487      

In [ ]:
# # Filtrar el DataFrame usando la función query
# filtered_df = fever_plans_df.query('SCORE > 0.6')

# # Imprimir el DataFrame resultante
# filtered_df

In [428]:
# # Agrupar por 'ID_PLAN' y 'DS_PLAN' y seleccionar la fila con el score máximo en cada grupo
# fever_plans_df = fever_plans_df.loc[fever_plans_df.groupby(['ID_PLAN', 'KW'])['SCORE'].idxmax()]

# # Reiniciar el índice del DataFrame resultante
# fever_plans_df = fever_plans_df.reset_index(drop=True)

# # Imprimir el DataFrame resultante
# fever_plans_df


In [26]:
# from keybert import KeyBERT

In [37]:
# kw_model = KeyBERT(model='distiluse-base-multilingual-cased-v1')

In [58]:
# from keybert import KeyBERT
# from nltk.corpus import stopwords
# import nltk
# nltk.download('stopwords')

# # Texto de entrada
# text = "Tu texto de entrada aquí"

# # Tokeniza el texto y elimina las stopwords en inglés
# stop_words = set(stopwords.words("spanish"))
# words = text.split()
# filtered_words = [word for word in words if word.lower() not in stop_words]
# filtered_text = ' '.join(filtered_words)

# # Aplica KeyBERT al texto preprocesado
# model = KeyBERT('distilbert-base-nli-mean-tokens')
# keywords = model.extract_keywords(filtered_text)

# print(keywords)

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\FEVER\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


[('texto', 0.8765), ('aquí', 0.8162), ('entrada', 0.7724)]


In [59]:
# from itertools import combinations

# # Palabras clave después de eliminar las stopwords
# keywords = ['texto', 'entrada', 'aquí']

# # Rango de ventanas que deseas considerar
# window_range = (1, 3)

# # Número máximo de combinaciones a guardar
# top_n = 5

# # Lista para almacenar las combinaciones de palabras clave
# keyword_combinations = []

# # Itera a través de las ventanas en el rango especificado
# for window_size in range(window_range[0], window_range[1] + 1):
#     # Genera todas las combinaciones de palabras clave para la ventana actual
#     combinations_for_window = list(combinations(keywords, window_size))
    
#     # Agrega las combinaciones a la lista de resultados
#     keyword_combinations.extend([' '.join(comb) for comb in combinations_for_window])

# # Limita el número de combinaciones a las primeras "top_n"
# keyword_combinations = keyword_combinations[:top_n]

# # Imprime las combinaciones resultantes
# for combination in keyword_combinations:
#     print(combination)


texto
entrada
aquí
texto entrada
texto aquí
